##### Copyright 2020 The TensorFlow Authors.

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# 모델 평균

<table class="tfo-notebook-buttons" align="left">
  <td><a target="_blank" href="https://www.tensorflow.org/addons/tutorials/average_optimizers_callback"><img src="https://www.tensorflow.org/images/tf_logo_32px.png">TensorFlow.org에서 보기</a></td>
  <td><a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/ko/addons/tutorials/average_optimizers_callback.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png">Google Colab에서 실행하기</a></td>
  <td><a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/ko/addons/tutorials/average_optimizers_callback.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png">GitHub에서 소스 보기</a></td>
      <td><a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/ko/addons/tutorials/average_optimizers_callback.ipynb"><img src="https://www.tensorflow.org/images/download_logo_32px.png">노트북 다운로드하기</a></td>
</table>


## 개요

이 노트북은 TensorFlow Addons 패키지의 모델 평균 체크포인트와 함께 Moving Average Optimizer를 사용하는 방법을 보여줍니다.


## 이동 평균

> 이동 평균의 장점은 최신 배치에서 급격한 손실 이동이나 불규칙한 데이터 표현에 덜 취약하다는 것입니다. 어느 시점까지는 모델 훈련에 대한 좀 더 일반적인 아이디어를 제공합니다.

## 확률적 평균

> Stocastic Weight Averaging(SWA)은 더 넓은 최적값으로 수렴됩니다. 기하학적 앙상블링과 비슷하게 됩니다. SWA는 다른 옵티마이저의 래퍼로 사용될 때 모델 성능을 개선하고 내부 옵티마이저의 서로 다른 궤적 포인트에서 결과를 평균화하는 간단한 방법입니다.

## 모델 평균 체크포인트

> `callbacks.ModelCheckpoint`는 훈련 중에 이동 평균 가중치를 저장하는 옵션을 제공하지 않습니다. 따라서 Moving Average Optimizer에서 사용자 정의 콜백이 필요합니다. `update_weights` 매개변수와 `ModelAverageCheckpoint`를 사용하면 다음이 가능합니다.

1. 이동 평균 가중치를 모델에 할당하고 저장합니다.
2. 이전의 평균이 아닌 가중치를 유지하지만, 저장된 모델은 평균 가중치를 사용합니다.

## 설정

In [2]:
!pip install -q -U tensorflow-addons

In [3]:
import tensorflow as tf
import tensorflow_addons as tfa

In [4]:
import numpy as np
import os

## 모델 빌드하기 

In [5]:
def create_model(opt):
    model = tf.keras.models.Sequential([
        tf.keras.layers.Flatten(),                         
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dense(10, activation='softmax')
    ])

    model.compile(optimizer=opt,
                    loss='sparse_categorical_crossentropy',
                    metrics=['accuracy'])

    return model

## 데이터세트 준비하기

In [6]:
#Load Fashion MNIST dataset
train, test = tf.keras.datasets.fashion_mnist.load_data()

images, labels = train
images = images/255.0
labels = labels.astype(np.int32)

fmnist_train_ds = tf.data.Dataset.from_tensor_slices((images, labels))
fmnist_train_ds = fmnist_train_ds.shuffle(5000).batch(32)

test_images, test_labels = test

 8192/29515 [=======>......................] - ETA: 0s

32768/29515 [=================================] - 0s 0us/step


    8192/26421880 [..............................] - ETA: 0s

 4292608/26421880 [===>..........................] - ETA: 0s

 9912320/26421880 [==========>...................] - ETA: 0s

...

21159936/26421880 [=======================>......] - ETA: 0s

26427392/26421880 [==============================] - 0s 0us/step


8192/5148 [===============================================] - 0s 0us/step


   8192/4422102 [..............................] - ETA: 0s

4423680/4422102 [==============================] - 0s 0us/step


여기에서는 3가지 옵티마이저를 비교할 것입니다.

- 래핑되지 않은 SGD
- 이동 평균을 사용하는 SGD
- 확률적 가중치 평균을 사용하는 SGD

같은 모델에서 어떻게 동작하는지 확인합니다.

In [7]:
#Optimizers 
sgd = tf.keras.optimizers.SGD(0.01)
moving_avg_sgd = tfa.optimizers.MovingAverage(sgd)
stocastic_avg_sgd = tfa.optimizers.SWA(sgd)

`MovingAverage` 및 `StocasticAverage` 옵티마이저 모두 `ModelAverageCheckpoint`를 사용합니다.

In [8]:
#Callback 
checkpoint_path = "./training/cp-{epoch:04d}.ckpt"
checkpoint_dir = os.path.dirname(checkpoint_path)

cp_callback = tf.keras.callbacks.ModelCheckpoint(filepath=checkpoint_dir,
                                                 save_weights_only=True,
                                                 verbose=1)
avg_callback = tfa.callbacks.AverageModelCheckpoint(filepath=checkpoint_dir, 
                                                    update_weights=True)

## 모델 훈련하기


### Vanilla SGD 옵티마이저 

In [9]:
#Build Model
model = create_model(sgd)

#Train the network
model.fit(fmnist_train_ds, epochs=5, callbacks=[cp_callback])

Epoch 1/5


   1/1875 [..............................] - ETA: 22:59 - loss: 2.2836 - accuracy: 0.1250

  25/1875 [..............................] - ETA: 3s - loss: 2.2489 - accuracy: 0.1527   

  50/1875 [..............................] - ETA: 3s - loss: 2.1985 - accuracy: 0.1953

  75/1875 [>.............................] - ETA: 3s - loss: 2.1498 - accuracy: 0.2403

...

1823/1875 [============================>.] - ETA: 0s - loss: 0.4078 - accuracy: 0.8563

1849/1875 [============================>.] - ETA: 0s - loss: 0.4078 - accuracy: 0.8563

1875/1875 [==============================] - ETA: 0s - loss: 0.4078 - accuracy: 0.8563

1875/1875 [==============================] - 4s 2ms/step - loss: 0.4078 - accuracy: 0.8563



Epoch 00005: saving model to ./training


In [10]:
#Evalute results
model.load_weights(checkpoint_dir)
loss, accuracy = model.evaluate(test_images, test_labels, batch_size=32, verbose=2)
print("Loss :", loss)
print("Accuracy :", accuracy)

313/313 - 0s - loss: 79.6013 - accuracy: 0.8019


Loss : 79.60128021240234
Accuracy : 0.8019000291824341


### 이동 평균 SGD

In [11]:
#Build Model
model = create_model(moving_avg_sgd)

#Train the network
model.fit(fmnist_train_ds, epochs=5, callbacks=[avg_callback])

Epoch 1/5


   1/1875 [..............................] - ETA: 17:07 - loss: 2.3389 - accuracy: 0.1250

  22/1875 [..............................] - ETA: 4s - loss: 2.2214 - accuracy: 0.2249   

  43/1875 [..............................] - ETA: 4s - loss: 2.1810 - accuracy: 0.2657

  64/1875 [>.............................] - ETA: 4s - loss: 2.1446 - accuracy: 0.2962

...

1822/1875 [============================>.] - ETA: 0s - loss: 0.4222 - accuracy: 0.8532

1845/1875 [============================>.] - ETA: 0s - loss: 0.4222 - accuracy: 0.8531

1868/1875 [============================>.] - ETA: 0s - loss: 0.4221 - accuracy: 0.8531

1875/1875 [==============================] - 4s 2ms/step - loss: 0.4221 - accuracy: 0.8531


INFO:tensorflow:Assets written to: ./training/assets


In [12]:
#Evalute results
model.load_weights(checkpoint_dir)
loss, accuracy = model.evaluate(test_images, test_labels, batch_size=32, verbose=2)
print("Loss :", loss)
print("Accuracy :", accuracy)

313/313 - 0s - loss: 79.6013 - accuracy: 0.8019


Loss : 79.60128021240234
Accuracy : 0.8019000291824341


### 확률적 가중치 평균 SGD 

In [13]:
#Build Model
model = create_model(stocastic_avg_sgd)

#Train the network
model.fit(fmnist_train_ds, epochs=5, callbacks=[avg_callback])

Epoch 1/5


   1/1875 [..............................] - ETA: 25:25 - loss: 2.2949 - accuracy: 0.2812

  19/1875 [..............................] - ETA: 5s - loss: 2.3291 - accuracy: 0.1629   

  37/1875 [..............................] - ETA: 5s - loss: 2.2916 - accuracy: 0.1835

  56/1875 [..............................] - ETA: 5s - loss: 2.2534 - accuracy: 0.2065

...

1826/1875 [============================>.] - ETA: 0s - loss: 0.5243 - accuracy: 0.8198

1845/1875 [============================>.] - ETA: 0s - loss: 0.5241 - accuracy: 0.8198

1864/1875 [============================>.] - ETA: 0s - loss: 0.5240 - accuracy: 0.8198

1875/1875 [==============================] - 5s 3ms/step - loss: 0.5239 - accuracy: 0.8199


INFO:tensorflow:Assets written to: ./training/assets


In [14]:
#Evalute results
model.load_weights(checkpoint_dir)
loss, accuracy = model.evaluate(test_images, test_labels, batch_size=32, verbose=2)
print("Loss :", loss)
print("Accuracy :", accuracy)

313/313 - 0s - loss: 79.6013 - accuracy: 0.8019


Loss : 79.60128021240234
Accuracy : 0.8019000291824341
